In [1]:
#Librerias necesarias para implementacion de algoritmo genetico
from __future__ import print_function

from evolver import Evolver

from tqdm import tqdm

import logging

import sys


# Aplicacion del Modelo
Aqui se aplica directamente el modelo descrito implementando el algoritmo genetico

In [2]:
#Librerias necesarias para trabajar con datasets
import pandas as pd
import numpy as np
from sklearn import linear_model, model_selection

#Librerias necesarias para aplicar redes neuronales
import tensorflow as tf
pd.set_option('display.max_columns', None)
df= pd.read_csv("Historial_Alumnos.csv", sep=",",index_col=False)
df.head()

id_anony Cod.Car.Sec  Cod.Car.Sec Codificado  Materia_1  \
0      2838  MCT-PLS13                     28.0  CALCULO 1   
1      4037  MCT-PLS13                     28.0  CALCULO 1   
2      4061  MCT-PLS13                     28.0  CALCULO 1   
3      4062  MCT-PLS13                     28.0  CALCULO 1   
4      4065  MCT-PLS13                     28.0  CALCULO 1   

   Materia_1 codificada  Anho_F_1  ciclo_F_1  Recursante_1  P1_F_1  P2_F_1  \
0                  33.0    2013.0        2.0           1.0     0.0    17.0   
1                  33.0    2015.0        2.0           1.0    16.0    19.0   
2                  33.0    2015.0        2.0           1.0    14.0    27.0   
3                  33.0    2015.0        2.0           1.0     5.0    24.0   
4                  33.0    2015.0        2.0           1.0    19.0    30.0   

   T_F_1  NotaFinal_1  Materia_1 Nota=1  Materia_1 Nota=2  Materia_1 Nota=3  \
0    8.0          2.0               0.0               1.0               0.0   
1    8.0          5.0               0.0               0.0               0.0   
2    8.0          3.0               0.0               0.0               1.0   
3    6.0          2.0               0.0               1.0               0.0   
4    9.0          5.0               0.0               0.0               0.0   

   Materia_1 Nota=4  Materia_1 Nota=5  Abandono la Materia 1  Materia_2  \
0               0.0               0.0                    1.0  CALCULO 2   
1               0.0               1.0                    0.0  CALCULO 2   
2               0.0               0.0                    0.0  CALCULO 2   
3               0.0               0.0                    0.0  CALCULO 2   
4               0.0               1.0                    0.0  CALCULO 2   

   Materia_2 codificada  Anho_F_2  ciclo_F_2  Recursante_2  P1_F_2  P2_F_2  \
0                  34.0    2014.0        1.0           1.0    11.0    16.0   
1                  34.0    2016.0        1.0           1.0    22.0    31.0   
2                  34.0    2016.0        1.0           1.0    13.0    23.0   
3                  34.0    2016.0        1.0           1.0    21.0    19.0   
4                  34.0    2016.0        1.0           1.0    24.0    29.0   

   T_F_2  NotaFinal_2  Materia_2 Nota=1  Materia_2 Nota=2  Materia_2 Nota=3  \
0    8.0          2.0               0.0               1.0               0.0   
1    7.0          5.0               0.0               0.0               0.0   
2    5.0          2.0               0.0               1.0               0.0   
3    5.0          2.0               0.0               1.0               0.0   
4    9.0          5.0               0.0               0.0               0.0   

   Materia_2 Nota=4  Materia_2 Nota=5  Abandono la Materia 2  Materia_3  \
0               0.0               0.0                    0.0  CALCULO 3   
1               0.0               1.0                    0.0  CALCULO 3   
2               0.0               0.0                    0.0  CALCULO 3   
3               0.0               0.0                    0.0  CALCULO 3   
4               0.0               1.0                    0.0  CALCULO 3   

   Materia_3 codificada  Anho_F_3  ciclo_F_3  Recursante_3  P1_F_3  P2_F_3  \
0                  35.0    2016.0        2.0           1.0    10.0     7.0   
1                  35.0    2016.0        2.0           1.0     6.0     9.0   
2                  35.0    2016.0        2.0           1.0    17.0    10.0   
3                  35.0    2016.0        2.0           1.0     5.0    18.0   
4                  35.0    2016.0        2.0           1.0    22.0    20.0   

   T_F_3  NotaFinal_3  Materia_3 Nota=1  Materia_3 Nota=2  Materia_3 Nota=3  \
0    2.0          2.0               0.0               1.0               0.0   
1    8.0          4.0               0.0               0.0               0.0   
2    8.0          2.0               0.0               1.0               0.0   
3    6.0          2.0               0.0               1

Antes que nada, es necesario preparar los datos que la red neuronal solicita para poder procesar la opcion mas viable para nuestro analisis

In [3]:
data=df[['Materia_1 codificada','Anho_F_1','ciclo_F_1','Recursante_1','P1_F_1','P2_F_1','T_F_1','NotaFinal_1','Abandono la Materia 1','Materia_2 codificada','Anho_F_2','ciclo_F_2','Recursante_2','P1_F_2','P2_F_2','T_F_2','NotaFinal_2','Abandono la Materia 2']]

[filas,columnas]=data.shape
labels=df[['Materia_3 Nota=2']]

#Como labels figura como string, es necesario cambiarlos a valores enteros
data = np.array(data)
labels = np.array(labels)
labels=np.ravel(labels)

#Verificamos las dimensiones de data y labels
display(np.shape(labels))
display(np.shape(data))

(56,)

(56, 18)

Los datos que el algoritmo genetico solicita a lo largo de su procesamiento son data, labels y columnas. Para facilitar dichos datos del notebook al algoritmo genetico, se emplea la libreria pickle

In [4]:
from pickle import dump,load
dump(data, open('data.pkl', 'wb'))
dump(labels, open('labels.pkl', 'wb'))
dump(columnas, open('columnas.pkl', 'wb'))

Una vez definidos apropiadamente estos parametros, se procede a realizar el procesamiento con el algoritmo genetico

In [5]:
import main as ge
lista=ge.main()

07/07/2021 10:25:20 AM - INFO - ***generate(generations, population, all_possible_genes, dataset)***
07/07/2021 10:25:20 AM - INFO - ***Now in generation 1 of 50***
07/07/2021 10:25:20 AM - INFO - --------------------------------------------------------------------------------
07/07/2021 10:25:20 AM - INFO - {'nb_layers': 5, 'activation': 'sigmoid', 'optimizer': 'adam', 'nb_neurons': [64, 16, 32, 64, 128, 32]}
07/07/2021 10:25:20 AM - INFO - Acc: 0.00%
07/07/2021 10:25:20 AM - INFO - UniID: 1
07/07/2021 10:25:20 AM - INFO - Mom and Dad: 0 0
07/07/2021 10:25:20 AM - INFO - Gen: 1
07/07/2021 10:25:20 AM - INFO - Hash: 1df3b97b086864fc4b7380aacd279066
07/07/2021 10:25:20 AM - INFO - {'nb_layers': 1, 'activation': 'sigmoid', 'optimizer': 'adamax', 'nb_neurons': [64, 32, 128, 16, 16, 128]}
07/07/2021 10:25:20 AM - INFO - Acc: 0.00%
07/07/2021 10:25:20 AM - INFO - UniID: 2
07/07/2021 10:25:20 AM - INFO - Mom and Dad: 0 0
07/07/2021 10:25:20 AM - INFO - Gen: 1
07/07/2021 10:25:20 AM - INFO - 

07/07/2021 10:25:20 AM - INFO - {'nb_layers': 2, 'activation': 'relu', 'optimizer': 'adam', 'nb_neurons': [32, 16, 64, 128, 16, 16]}
07/07/2021 10:25:20 AM - INFO - Acc: 0.00%
07/07/2021 10:25:20 AM - INFO - UniID: 22
07/07/2021 10:25:20 AM - INFO - Mom and Dad: 0 0
07/07/2021 10:25:20 AM - INFO - Gen: 1
07/07/2021 10:25:20 AM - INFO - Hash: 4c29e43a2e54c1ac12cc4e7cd788a154
07/07/2021 10:25:20 AM - INFO - {'nb_layers': 1, 'activation': 'softmax', 'optimizer': 'adam', 'nb_neurons': [128, 128, 32, 128, 64, 32]}
07/07/2021 10:25:20 AM - INFO - Acc: 0.00%
07/07/2021 10:25:20 AM - INFO - UniID: 23
07/07/2021 10:25:20 AM - INFO - Mom and Dad: 0 0
07/07/2021 10:25:20 AM - INFO - Gen: 1
07/07/2021 10:25:20 AM - INFO - Hash: 23055f63830a520c70e176a4bfae5cb2
07/07/2021 10:25:20 AM - INFO - {'nb_layers': 1, 'activation': 'sigmoid', 'optimizer': 'adam', 'nb_neurons': [64, 16, 64, 64, 128, 128]}
07/07/2021 10:25:20 AM - INFO - Acc: 0.00%
07/07/2021 10:25:20 AM - INFO - UniID: 24
07/07/2021 10:25:20

***Dataset: dataset
***Evolving for 50 generations with population size = 30***
(44,)
(44, 18)
(44, 2)
(44, 18)
(44, 18)
(44, 2)
Epoch 1/50
1/1 [==============================] - 0s 166ms/step - loss: 0.7445 - accuracy: 0.4545 - val_loss: 0.6682 - val_accuracy: 0.7500
Epoch 2/50
1/1 [==============================] - 0s 12ms/step - loss: 0.7170 - accuracy: 0.5227 - val_loss: 0.6161 - val_accuracy: 0.7500
Epoch 3/50
1/1 [==============================] - 0s 12ms/step - loss: 0.5607 - accuracy: 0.7273 - val_loss: 0.5828 - val_accuracy: 0.7500


  3%|▎         | 1/30 [00:01<00:33,  1.17s/it]07/07/2021 10:25:21 AM - INFO - Getting Keras datasets
07/07/2021 10:25:21 AM - INFO - Compling Keras model
07/07/2021 10:25:21 AM - INFO - Architecture:[64, 32, 128, 16, 16, 128],sigmoid,adamax,1


Test loss: 0.5828276872634888
Test accuracy: 0.75

 Modelo mas eficiente creado 

(44,)
(44, 18)
(44, 2)
(44, 18)
(44, 18)
(44, 2)
Epoch 1/50
1/1 [==============================] - 0s 104ms/step - loss: 0.4042 - accuracy: 0.8636 - val_loss: 0.6016 - val_accuracy: 0.7500
Epoch 2/50
1/1 [==============================] - 0s 10ms/step - loss: 0.4591 - accuracy: 0.8636 - val_loss: 0.6020 - val_accuracy: 0.7500
Epoch 3/50
1/1 [==============================] - 0s 10ms/step - loss: 0.3988 - accuracy: 0.8636 - val_loss: 0.6025 - val_accuracy: 0.7500


...

 98%|█████████▊| 52/53 [00:36<00:00,  1.26it/s]07/07/2021 10:50:02 AM - INFO - Getting Keras datasets
07/07/2021 10:50:02 AM - INFO - Compling Keras model
07/07/2021 10:50:02 AM - INFO - Architecture:[64, 64, 128, 64, 128, 128],relu,adam,2


Test loss: 0.6016528010368347
Test accuracy: 0.75
(44,)
(44, 18)
(44, 2)
(44, 18)
(44, 18)
(44, 2)
Epoch 1/50


07/07/2021 10:50:02 AM - WARNING - 5 out of the last 13 calls to <function Model.make_train_function.<locals>.train_function at 0x000002695F5153A0> triggered tf.function retracing. Tracing is expensive and the excessive number of tracings could be due to (1) creating @tf.function repeatedly in a loop, (2) passing tensors with different shapes, (3) passing Python objects instead of tensors. For (1), please define your @tf.function outside of the loop. For (2), @tf.function has experimental_relax_shapes=True option that relaxes argument shapes that can avoid unnecessary retracing. For (3), please refer to https://www.tensorflow.org/tutorials/customization/performance#python_or_tensor_args and https://www.tensorflow.org/api_docs/python/tf/function for  more details.


1/1 [==============================] - 0s 125ms/step - loss: 0.5751 - accuracy: 0.8182 - val_loss: 0.5890 - val_accuracy: 0.7500
Epoch 2/50
1/1 [==============================] - 0s 13ms/step - loss: 0.5358 - accuracy: 0.7955 - val_loss: 0.5712 - val_accuracy: 0.7500
Epoch 3/50
1/1 [==============================] - 0s 14ms/step - loss: 0.5068 - accuracy: 0.8864 - val_loss: 0.5574 - val_accuracy: 0.7500
Test loss: 0.5573941469192505
Test accuracy: 0.75


100%|██████████| 53/53 [00:37<00:00,  1.40it/s]
07/07/2021 10:50:03 AM - INFO - Generation average: 65.25%
07/07/2021 10:50:03 AM - INFO - --------------------------------------------------------------------------------
07/07/2021 10:50:03 AM - INFO - --------------------------------------------------------------------------------
07/07/2021 10:50:03 AM - INFO - {'activation': 'relu', 'nb_layers': 2, 'optimizer': 'adam', 'nb_neurons': [16, 64, 128, 32, 128, 128]}
07/07/2021 10:50:03 AM - INFO - Acc: 91.67%
07/07/2021 10:50:03 AM - INFO - UniID: 143
07/07/2021 10:50:03 AM - INFO - Mom and Dad: 121 18
07/07/2021 10:50:03 AM - INFO - Gen: 6
07/07/2021 10:50:03 AM - INFO - Hash: d73aaebc429f8dfc78965f2a4d4660f1
07/07/2021 10:50:03 AM - INFO - {'activation': 'relu', 'nb_layers': 2, 'optimizer': 'adamax', 'nb_neurons': [64, 64, 128, 32, 128, 64]}
07/07/2021 10:50:03 AM - INFO - Acc: 91.67%
07/07/2021 10:50:03 AM - INFO - UniID: 642
07/07/2021 10:50:03 AM - INFO - Mom and Dad: 143 87
07/07/20